# Анализ данных

Посмотрим на тренировочный датасет, как конкретно находится нужный фрагмент и выявим паттерны для использования в будущей модели

In [32]:
import json


In [59]:
f = open('data/train.json')
dataJSON = json.load(f)
f.close()

for row in dataJSON:
    for key, value in row.items():
        print(key, ":", value)


FileNotFoundError: [Errno 2] No such file or directory: 'dataset/train.json'

In [34]:
def get_label(label):
    return label != "обеспечение исполнения контракта"


In [35]:
from pandas import DataFrame, concat


Сформируем датафрейм из `extracted_part`

In [36]:
df = DataFrame()

for item in dataJSON:

    dict_ext = {'label': int(get_label(item['label'])),
                'start': item['extracted_part']['answer_start'],
                'stop': item['extracted_part']['answer_end'],
                'text': item['extracted_part']['text']
                }

    df = concat([df, DataFrame(dict_ext, index=[item['id']])])


df.insert(3, 'length', df['stop'] - df['start'])
df


label  start  stop  length  \
809436509      0   1279  1343      64   
854885310      0   1222  1318      96   
4382157        0   1297  1343      46   
184555082      0   1304  1350      46   
211645258      0   1302  1348      46   
...          ...    ...   ...     ...   
938335285      1   1213  1402     189   
214609521      1      0     0       0   
94811748       1      0     0       0   
903507299      1      0     0       0   
926039184      1      0     0       0   

                                                        text  
809436509  Размер обеспечения исполнения контракта 6593.2...  
854885310  Поставщик должен предоставить обеспечение испо...  
4382157       Размер обеспечения исполнения контракта 10.00%  
184555082     Размер обеспечения исполнения контракта 10.00%  
211645258     Размер обеспечения исполнения контракта 10.00%  
...                                                      ...  
938335285  Заказчиком установлено требование обеспечения ...  
214609521                                                     
94811748                                                      
903507299                                                     
926039184                                                     

[1799 rows x 5 columns]

Оставим только записи с найденными фрагментами

In [37]:
df_ = df.drop(df[df['length'] == 0].index)
df_


label  start  stop  length  \
809436509      0   1279  1343      64   
854885310      0   1222  1318      96   
4382157        0   1297  1343      46   
184555082      0   1304  1350      46   
211645258      0   1302  1348      46   
...          ...    ...   ...     ...   
799382195      1   1281  1475     194   
611045142      1   1235  1364     129   
718284263      1   1250  1417     167   
569335063      1   1235  1489     254   
938335285      1   1213  1402     189   

                                                        text  
809436509  Размер обеспечения исполнения контракта 6593.2...  
854885310  Поставщик должен предоставить обеспечение испо...  
4382157       Размер обеспечения исполнения контракта 10.00%  
184555082     Размер обеспечения исполнения контракта 10.00%  
211645258     Размер обеспечения исполнения контракта 10.00%  
...                                                      ...  
799382195  срок действия гарантийных обязательств не мене...  
611045142  Размер обеспечения исполнения гарантийных обяз...  
718284263  Размер обеспечения исполнения гарантийных обяз...  
569335063  Субподрядчик в качестве обеспечения надлежащег...  
938335285  Заказчиком установлено требование обеспечения ...  

[1492 rows x 5 columns]

По статистикам можно только отметить среднюю длину фрагмента, в целом больше ничего

In [38]:
df_['length'].describe()


count    1492.000000
mean      105.971180
std        45.641679
min        34.000000
25%        69.000000
50%       101.000000
75%       133.000000
max       302.000000
Name: length, dtype: float64

Отсутствует почти пятая часть ответов

In [39]:
_ = df_.shape[0]

print('gaps: {:.1f}%'.format((1 - _/df.shape[0])*100))

gaps: 17.1%


Почти во всех найденных фрагментах найдено число. Есть небольшая вероятность, что это оформление пункта, но в подавляющем большинстве - это сумма выраженная как номинально через валюту или в процентном виде
#
В большинстве фрагменты начинаются с заглавной буквы, однако сегментировать текст исключительно по такому правилу скорее всего не получится

In [40]:
_ = df_.shape[0]

digit_entr = upper_entr = pr_entr = 0

for s in df_.iloc[:, -1]:
    digit_entr += any(char.isdigit() for char in s)
    upper_entr += s[0].isupper()
    pr_entr += any(char == '%' for char in s)

print('include any digit: {:.1f}%'.format(digit_entr/_*100))
print('upper start strings: {:.1f}%'.format(upper_entr/_*100))
print('include [%]: {:.1f}%'.format(pr_entr/_*100))

include any digit: 99.0%
upper start strings: 91.6%
include [%]: 70.1%


Теперь посмотрим на включение слов из указанного пункта анкеты и добавим слово `размер`, 
так как чаще всего речь идёт о сумме

In [41]:
from natasha import (
    Segmenter,
    MorphVocab,

    NewsEmbedding,
    NewsMorphTagger,
    Doc
)

segmenter = Segmenter()
morph_vocab = MorphVocab()
emb = NewsEmbedding()
morph_tagger = NewsMorphTagger(emb)


In [42]:
label0 = {'размер': 0,
          'договор': 0,
          'обеспечение': 0,
          'исполнение': 0,
          'контракт': 0}

label1 = {'размер': 0,
          'договор': 0,
          'обеспечение': 0,
          'гарантийный': 0,
          'обязательство': 0, }

df_l0 = df_.drop(df_[df_['label'] != 0].index)
df_l1 = df_.drop(df_[df_['label'] == 0].index)

In [43]:
def get_lemma_entr(search, label):

    for _ in search:

        try:
            for __ in label.keys():
                label[__] += [0]
        except:
            next

        doc = Doc(_)
        doc.segment(segmenter)
        doc.tag_morph(morph_tagger)

        for token in doc.tokens:
            token.lemmatize(morph_vocab)

            for __ in label.keys():

                try:
                    label[__] += token.lemma == __
                except:
                    label[__][-1] += token.lemma == __

    return label


def print_lemma_entr(df, label):

    label = get_lemma_entr(search=df['text'], label=label)

    try:
        return {_:  '{:.1f}%'.format(label[_]/df.shape[0]*100) for _ in label}
    except:
        return DataFrame(label, index=df.index).drop_duplicates()


Для пункта `обеспечение исполнения контракта` высокое процентное включение всех слов
# 
Однако не 100%, причем как в большую так и меньшую сторону  
Некоторое слова включены по несколько раз
# 
Другие не включены вовсе

In [44]:
_ = label0

print_lemma_entr(label=_, df=df_l0)

{'размер': '93.8%',
 'договор': '81.9%',
 'обеспечение': '103.0%',
 'исполнение': '97.9%',
 'контракт': '89.8%'}

Аналогично для пункта `обеспечение гарантийных обязательств`

In [45]:
_ = label1

print_lemma_entr(label=_, df=df_l1)

{'размер': '96.5%',
 'договор': '23.8%',
 'обеспечение': '108.7%',
 'гарантийный': '105.5%',
 'обязательство': '104.7%'}

Теперь выведем конкретное включение в каждый фрагмент для каждой леммы и рассмотрим где меньшее кол-во вхождений

In [46]:
_ = {'размер': [],
     'договор': [],
     'обеспечение': [],
     'исполнение': [],
     'контракт': []}

__ = df_l0

# print_lemma_entr(label=_, df=__)

_ = print_lemma_entr(label=_, df=__)
concat([_, df_.loc[_.index, 'text']], axis=1).style.hide_index()

C:\Users\gmr\AppData\Local\Temp\ipykernel_12940\3387024640.py:12: FutureWarning: this method is deprecated in favour of `Styler.hide(axis="index")`
  concat([_, df_.loc[_.index, 'text']], axis=1).style.hide_index()


In [47]:
_ = {'размер': [],
     'договор': [],
     'обеспечение': [],
     'гарантийный': [],
     'обязательство': [], }

__ = df_l1

# print_lemma_entr(label=_, df=__)

_ = print_lemma_entr(label=_, df=df_l1)
concat([_, df_.loc[_.index, 'text']], axis=1)

размер  договор  обеспечение  гарантийный  обязательство  \
195864972       1        0            1            1              1   
56810761        2        0            1            1              1   
347302088       0        0            1            1              1   
213192442       1        1            1            1              1   
152642150       0        2            2            1              1   
468053403       1        2            1            1              1   
887278573       0        2            1            1              1   
961852032       0        1            1            1              1   
353919950       2        1            1            1              1   
890468784       1        0            1            2              1   
331036917       2        0            2            2              2   
638477631       1        0            3            1              1   
405862183       1        0            1            2              2   
999135353       1        0            3            2              2   
127269228       1        3            2            1              1   
659495625       1        0            2            2              2   
610623613       1        1            2            2              2   
40461135        1        2            2            2              2   
805343253       1        2            3            1              1   
941320396       0        0            2            2              2   
562568545       0        1            2            1              1   
753831315       2        2            4            2              2   
311939548       2        1            2            1              2   
599798630       2        1            2            2              2   
116134205       1        3            3            1              1   
976728439       2        2            1            1              1   
611794687       2        0            1            2              2   
707080403       1        2            3            2              2   
871024989       0        3            2            2              2   
569335063       1        3            1            2              1   

                                                        text  
195864972  Размер обеспечения гарантийных обязательств 15...  
56810761   Размер обеспечения гарантийных обязательств по...  
347302088   Обеспечение гарантийных обязательств 5% от НМЦК.  
213192442  Размер обеспечения гарантийных обязательств не...  
152642150  Заказчиком установлено требование обеспечения ...  
468053403  Обеспечение исполнения гарантийных обязательст...  
887278573  Обеспечение гарантийных обязательств по Догово...  
961852032  Обеспечение гарантийных обязательств по Догово...  
353919950  Размер обеспечения гарантийных обязательств 2,...  
890468784  на протяжении указанного в Контракте гарантийн...  
331036917  Размер обеспечения гарантийных обязательств со...  
638477631  Размер обеспечения гарантийных обязательств, п...  
405862183  Обеспечение гарантийных обязательств устанавли...  
999135353  Размер обеспечения гарантийных обязательств 66...  
127269228  Требования к независимым гарантиям, предоставл...  
659495625  Обеспечение гарантийных обязательств Контракта...  
610623613  Генеральный подрядчик обязан предоставить Зака...  
40461135   согласно п. 3.1. Договора Поставщик представля...  
805343253  Размер обеспечения исполнения договора и/или о...  
941320396  взамен ранее предоставленного обеспечения гара...  
562568545  если Заказчиком установлено требование обеспеч...  
753831315   Размер обеспечения исполнения договора, разме...  
311939548  Размер обеспечения исполнения обязательств на ...  
599798630  Размер обеспечения гарантийных обязательств: у...  
116134205  Размер обеспечения исполнения Договора и (или)...  
976728439  Размер обеспечения исполнения договора (или) г...  
611794687  Размер обеспечения гарантийных обязательств ус...  
707080403  Обеспечение исполнения договора №_

In [48]:
import textwrap

In [49]:
def print_documents(indexs):

    _ = DataFrame(dataJSON)
    
    for i in indexs:
        __ = _.loc[_['id'] == i]
        print(textwrap.fill(__.iloc[0, 1], 100), '\n')

На примере `437809654` документа, фрагмент не содержит ни одной леммы из из пункта анкеты, но содержит сумму. Про описание пункта говорилось ранее, но фрагмент не содержит конкретные леммы, заменяя смысл контекстными синонимами, слова КОНТРАКТ отсутствует, используется понятие ДОГОВОР, вырезана валюта, проблемы, если использовать какой нибудь `MoneyExtractor` (предполагаю, данные размечивались не в ручную)

In [50]:
_ = [644238984, 853185282, 437809654, 787324095]
print(df_l0.loc[_, 'text'].to_markdown(), '\n')
print_documents(indexs = _)


|           | text                                                                                                 |
|----------:|:-----------------------------------------------------------------------------------------------------|
| 644238984 | Установить обеспечения исполнения контракта (от 0,5% до 30%) % обеспечения                           |
| 853185282 | Сумма обеспечения настоящего Договора составляет: 240 000,00 рублей.                                 |
| 437809654 | В размере 5% от начальной максимальной цены Договора в сумме 15801,15                                |
| 787324095 | Размер обеспечения договора установлен в размере 5% от начальной (максимальной) цены договора (лота) | 

Утверждена: Начальник МКУ «ХЭГ» ______________ Шигорин С. В наименование и описание объекта закупки,
условия контракта (РАЗДЕЛ 2 ИЗВЕЩЕНИЯ ОБ ОСУЩЕСТВЛЕНИИ ЗАКУПКИ) 1 Информация о заказчике
Бюджетополучатель: Муниципальное казенное учреждение «Хозяйственно-эксплуатационная ыть только
субъекты ма

С гарантийными обязательствами веселее, необязателно даже наличия суммы, но фрагмент считается найденным

In [51]:
_ = [941320396, 562568545, 890468784]
print(df_l1.loc[_, 'text'].to_markdown(), '\n')
print_documents(indexs = _)

|           | text                                                                                                                                                                                                                                     |
|----------:|:-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| 941320396 | взамен ранее предоставленного обеспечения гарантийных обязательств новое обеспечение гарантийных обязательств.                                                                                                                           |
| 562568545 | если Заказчиком установлено требование обеспечения исполнения договора и/или обеспечения исполнения гарантийных обязательств.                                                                                                            |
| 89

Тогда посмотрим на документы, где фрагменты не найдены совсем

In [52]:
df_nan = df.drop(df[df['length'] != 0].index)
df_nan

label  start  stop  length text
21387522       1      0     0       0     
988512459      1      0     0       0     
576814118      1      0     0       0     
33321982       1      0     0       0     
870221477      1      0     0       0     
...          ...    ...   ...     ...  ...
58251022       1      0     0       0     
214609521      1      0     0       0     
94811748       1      0     0       0     
903507299      1      0     0       0     
926039184      1      0     0       0     

[307 rows x 5 columns]

In [53]:
print_documents(indexs = df_nan.index)

Версия с 04.07.2022 года У Т В Е Р Ж Д А Ю «Государственное автономное учреждение Республики Саха
(Якутия) ''Республиканская больница №1 - Национальный центр медицины''» Подписано усиленной
квалифицированной электронной Версия с 04.07.2022 года У Т В Е Р Ж Д А Ю «Государственное автономное
учреждение Республики Саха (Якутия) ''Республиканская больница №1 - Национальный центр медицины''»
Подписано усиленной квалифицированной электронной подписью ДОКУМЕНТАЦИЯ О ПРОВЕДЕНИИ АУКЦИОНА (в
электронной форме) Номер и дата заявки: эа-2022-09-644 Заказчик ГАУ РС (Я) ''РБ№1-НЦМ'' Предмет
закупки: Поставка расходного материала для мониторирования глюкозы (эндокринологическое отделение)
для выполнения ВТМП Начальная (максимальная) цена договора: 228 760,00 рублей Содержание
документации об электронном аукционе Настоящая документация о проведении аукциона разработана в
соответствии с положениями: Гражданского кодекса Российской Федерации, Федерального закона от 18
июля 2011 года № 223-ФЗ «О закупках 

In [54]:
print_documents(indexs = df_.index)

Извещение о проведении открытого конкурса в электронной форме для закупки №0328300032822000806 Общая
информация Номер извещения 0328300032822000806 Наименование объекта закупки Поставка продуктов
питания Способ определения поставщика (подрядчика, исполнителя) Открытый конкурс в бль Порядок
внесения денежных средств в качестве обеспечения заявки на участие в закупке, а также условия
гарантии Обеспечение заявки на участие в закупке может предоставляться участником закупки в виде
денежных средств или независимой гарантии, предусмотренной ст. 45 Федерального закона № 44-ФЗ. Выбор
способа обеспечения осуществляется участником закупки самостоятельно. Срок действия независимой
гарантии должен составлять не менее месяца с даты окончания срока подачи заявок. Обеспечение заявки
на участие в закупке предоставляется в соответствии с ч. 5 ст. 44 Федерального закона № 44-ФЗ.
Условия независимой гарантии в соответствии со ст. 45 Федерального закона № 44-ФЗ. Реквизиты счета в
соответствии с п.16 ч. 1 

В целом, при указанном пункте анкеты хоть и находятся отдельные включения нужных лемм, тем не менее самой фразы в правильном формате нет

In [55]:
_ = {'размер': [],
     'сумма': [],
     'обеспечение': [],
     'исполнение': [],
     'контракт': [],
     'гарантийный': [],
     'обязательство': [], }

__ = DataFrame()

for i in df_nan.index:
    __ = concat([__, DataFrame(dataJSON).loc[DataFrame(dataJSON)['id'] == i]])

_ = get_lemma_entr(label=_, search=__['text'])
concat([DataFrame(_, index=df_nan.index), df_nan['label']], axis=1).drop_duplicates()

размер  сумма  обеспечение  исполнение  контракт  гарантийный  \
21387522        0      0            0           2         0            0   
988512459       0      0            0           0         0            0   
841199412       0      0            2           0         0            0   
530135745       0      0            1           0         0            0   
103381269       0      0            1           0         0            0   
842259306       0      0            0           0         0            0   
568278777       0      0            0           0         1            0   
41858643        0      0            0           1         0            0   
279678657       0      0            0           0         0            0   
410875162       0      0            0           0         0            0   
482313075       0      1            0           0         6            0   
894571448       0      0            1           0         4            0   
254389104       0      0            2           0         5            0   
123213155       0      0            1           0         4            0   
793891511       0      0            0           0         3            0   
58876711        0      0            0           0         5            0   
931962258       0      0            1           0         2            0   
908753490       0      0            1           0         1            0   
977032556       0      0            1           0         3            0   
30076414        0      0            0           0         4            0   
816725356       0      0            1           1         2            0   
163655004       0      0            1           0         5            0   
689018053       0      0            0           0         2            0   
701794530       0      0            0           0         4            0   
476192036       2      0            8           1         1            2   
175966212       0      0            2           0         1            0   
588528614       0      1            1           0         0            0   
100721352       0      1            0           0         0            0   
719126687       0      0            1           1         0            0   
833988154       0      0            0           1         0            0   
219363951       0      2            2           3         0            0   
471097685       0      0            5           3         0            0   
14015810        0      2            4           4         0            2   

           обязательство  label  
21387522               0      1  
988512459              0      1  
841199412              0      1  
530135745              0      1  
103381269              0      0  
842259306              1      1  
568278777              0      1  
41858643               0      1  
279678657              0      0  
410875162              3      0  
482313075              0      1  
894571448              0      1  
254389104              0      1  
123213155              1      1  
793891511              0      1  
58876711               0      1  
931962258              0      1  
908753490              0      1  
977032556              0      1  
30076414               0      1  
816725356              0      1  
163655004              0      1  
689018053              0      1  
701794530              1      1  
476192036              1      1  
175966212              0      1  
588528614              4      1  
100721352              0      1  
719126687              0      1  
833988154              1      1  
219363951              3      1  
471097685              2      1  
14015810               5      1

In [56]:
_ = [14015810]
print_documents(indexs = _)

Приложение № 9 к Договору № __ от «__»_____ г. Способы обеспечения исполнения обязательств
Поставщика Для закупочных процедур, проводимых только среди СМСП (редакция приложения должна быть
приведена в соответствии с условиями закупочной процедуры) 1-й Вариант (БГ на исполнение
обязательств по договору без обеспечения в гарантийный период) 1. В качестве способа обеспечения
надлежащего исполнения обязательств по Договору Поставщик по своему выбору в течение 20 дней с даты
подписания Договора обязуется предоставить Покупателю обеспечение в виде банковской гарантии
надлежащего исполнения обязательств или внесения денежных средств на расчетный счет Покупателя,
указанный в Договоре, в соответствии со ст.381.1 ГК РФ (далее – «обеспечительный платеж»). На сумму
обеспечительного платежа проценты, установленные статьей 317.1 ГК РФ, не начисляются. Датой внесения
обеспечительного платежа считается дата зачисления денежных средств на расчетный счет Покупателя. 1.
Банковская гарантия (обеспечительн

In [57]:
def get_size_doc(indexs):
    _ = DataFrame()

    for i in indexs:
        _ = concat([_, DataFrame(dataJSON).loc[DataFrame(dataJSON)['id'] == i]])


    __ = []

    for str in _['text']:
        __ += [len(str)]

    return __


Тогда глянем ещё на размер документов с найденными фрагментами и без

In [58]:
_ = get_size_doc(df_.index)
__ = get_size_doc(df_nan.index)

_ = concat([DataFrame({'include_label' : _}),
            DataFrame({'not' : __})],
            axis=1)

print(_.describe().to_markdown())

|       |   include_label |      not |
|:------|----------------:|---------:|
| count |        1492     |  307     |
| mean  |        2529.28  | 1194.49  |
| std   |         135.359 |  138.086 |
| min   |        1492     | 1002     |
| 25%   |        2443.75  | 1088     |
| 50%   |        2559     | 1186     |
| 75%   |        2622     | 1259     |
| max   |        3212     | 1645     |


### Выводы 
Регуляркой не решить(
***
- Почти гарантированно ответ является осмысленной фразой, но необязательно самостоятельным предложением в документе
- Почти гарантированно ответ содержит цифру или число. Это обычно денежная сумма или процент от суммы
- Почти гарантированно ответ содержит **хотя бы одно** слово из указанного пункта анкеты
#
- С очень высокой вероятностью ответ начинается с символа верхнего регистра
- С очень высокой вероятностью ответ содержит **несколько** слов из указанного пункта анкеты
#
- С очень высокой вероятностью ответ содержит слово 'размер' или 'сумма'
#
- С высокой вероятностью ответ содержит все слова из пункта анкеты
#
- С вероятностью выше среднего сумма указана в процентном виде
#
- Длина строки ответа в среднем около 100 +- 45 символов
- Текст документов без указанного пункта анкеты в среднем в два раза меньше других